In [4]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer 
import numpy as np
import pandas as pd
from sklearn.metrics import confusion_matrix, classification_report, accuracy_score, roc_auc_score
from sklearn.pipeline import Pipeline

In [5]:
import gensim.downloader
print(list(gensim.downloader.info()['models'].keys()))

['fasttext-wiki-news-subwords-300', 'conceptnet-numberbatch-17-06-300', 'word2vec-ruscorpora-300', 'word2vec-google-news-300', 'glove-wiki-gigaword-50', 'glove-wiki-gigaword-100', 'glove-wiki-gigaword-200', 'glove-wiki-gigaword-300', 'glove-twitter-25', 'glove-twitter-50', 'glove-twitter-100', 'glove-twitter-200', '__testing_word2vec-matrix-synopsis']


# GloVe

In [6]:
glove_model = gensim.downloader.load("glove-twitter-25")  # load glove vectors


In [7]:
print(glove_model['cat']) # word embedding for 'cat'
glove_model.most_similar("cat")  # show words that similar to word 'cat'

[-0.96419  -0.60978   0.67449   0.35113   0.41317  -0.21241   1.3796
  0.12854   0.31567   0.66325   0.3391   -0.18934  -3.325    -1.1491
 -0.4129    0.2195    0.8706   -0.50616  -0.12781  -0.066965  0.065761
  0.43927   0.1758   -0.56058   0.13529 ]


[('dog', 0.9590820074081421),
 ('monkey', 0.920357882976532),
 ('bear', 0.9143136739730835),
 ('pet', 0.9108031392097473),
 ('girl', 0.8880629539489746),
 ('horse', 0.8872726559638977),
 ('kitty', 0.8870542049407959),
 ('puppy', 0.886769711971283),
 ('hot', 0.886525571346283),
 ('lady', 0.8845519423484802)]

In [8]:
glove_model.similarity('cat', 'bus')

0.60927683

In [9]:
categories = ['alt.atheism', 'comp.graphics', 'sci.space'] 
remove = ('headers', 'footers', 'quotes')
twenty_train = fetch_20newsgroups(subset='train', shuffle=True, random_state=42, categories = categories, remove = remove )
twenty_test = fetch_20newsgroups(subset='test', shuffle=True, random_state=42, categories = categories, remove = remove )


# Векторизуем обучающую выборку
Получаем матрицу "Документ-термин"

In [10]:
vectorizer = CountVectorizer(stop_words='english')

In [11]:
train_data = vectorizer.fit_transform(twenty_train['data'])
CV_data=pd.DataFrame(train_data.toarray(), columns=vectorizer.get_feature_names_out())
print(CV_data.shape)
CV_data.head()

(1657, 23297)


00  000  0000  00000  000000  000005102000  000062david42  000100255pixel  \
0   0    0     0      0       0             0              0               0   
1   0    0     0      0       0             0              0               0   
2   0    0     0      0       0             0              0               0   
3   0    0     0      0       0             0              0               0   
4   0    0     0      0       0             0              0               0   

   00041032  0004136  ...  zurbrin  zurich  zus  zvi  zwaartepunten  zwak  \
0         0        0  ...        0       0    0    0              0     0   
1         0        0  ...        0       0    0    0              0     0   
2         0        0  ...        0       0    0    0              0     0   
3         0        0  ...        0       0    0    0              0     0   
4         0        0  ...        0       0    0    0              0     0   

   zwakke  zware  zwarte  zyxel  
0       0      0       0      0  
1       0      0       0      0  
2       0      0       0      0  
3       0      0       0      0  
4       0      0       0      0  

[5 rows x 23297 columns]

In [12]:
# Создадим список слов, присутствующих в словаре.
words_vocab=CV_data.columns
print(words_vocab[0:10])

Index(['00', '000', '0000', '00000', '000000', '000005102000', '000062david42',
       '000100255pixel', '00041032', '0004136'],
      dtype='object')


## Векторизуем с помощью GloVe

Нужно для каждого документа сложить glove-вектора слов, из которых он состоит.
В результате получим вектор документа как сумму векторов слов, из него состоящих

### Посмотрим на примере как будет работать векторизация

In [ ]:
text_data = ['Hello world I love python', 'This is a great computer game! 00 000 zyxel']
# Векторизуем с помощью обученного CountVectorizer
X = vectorizer.transform(text_data)
CV_text_data=pd.DataFrame(X.toarray(), columns=vectorizer.get_feature_names_out())
CV_text_data


In [ ]:
# Создадим датафрейм, в который будем сохранять вектор документа
glove_data=pd.DataFrame()

# Пробегаем по каждой строке (по каждому документу)
for i in range(CV_text_data.shape[0]):
    
    # Вектор одного документа с размерностью glove-модели:
    one_doc = np.zeros(25) 
    
    # Пробегаемся по каждому документу, смотрим, какие слова документа присутствуют в нашем словаре
    # Суммируем glove-вектора каждого известного слова в one_doc
    for word in words_vocab[CV_text_data.iloc[i,:] >= 1]:
        if word in glove_model.key_to_index.keys(): 
            print(word, ': ', glove_model[word])
            one_doc += glove_model[word]
    print(text_data[i], ': ', one_doc)
    glove_data=glove_data.append(pd.DataFrame([one_doc]))    
print('glove_data: ', glove_data)

In [ ]:
def text2vec(text_data):
    
    # Векторизуем с помощью обученного CountVectorizer
    X = vectorizer.transform(text_data)
    CV_text_data=pd.DataFrame(X.toarray(), columns=vectorizer.get_feature_names_out())
    CV_text_data
    # Создадим датафрейм, в который будем сохранять вектор документа
    glove_data=pd.DataFrame()

    # Пробегаем по каждой строке (по каждому документу)
    for i in range(CV_text_data.shape[0]):

        # Вектор одного документа с размерностью glove-модели:
        one_doc = np.zeros(25) 

        # Пробегаемся по каждому документу, смотрим, какие слова документа присутствуют в нашем словаре
        # Суммируем glove-вектора каждого известного слова в one_doc
        for word in words_vocab[CV_text_data.iloc[i,:] >= 1]:
            if word in glove_model.key_to_index.keys(): 
                #print(word, ': ', glove_model[word])
                one_doc += glove_model[word]
        #print(text_data[i], ': ', one_doc)
        glove_data = pd.concat([glove_data, pd.DataFrame([one_doc])], axis = 0)
    #print('glove_data: ', glove_data)
    return glove_data

In [ ]:

glove_data


In [ ]:
one_doc

In [ ]:
train_data_glove = text2vec(twenty_train['data']);
train_data_glove

In [ ]:
train_data


In [ ]:
clf = KNeighborsClassifier(n_neighbors = 5)

In [ ]:
clf.fit(train_data_glove, twenty_train['target'])

In [ ]:
test_data_glove = text2vec(twenty_test['data']);

In [ ]:
test_data_glove

In [ ]:
predict = clf.predict(test_data_glove )

In [ ]:
print (confusion_matrix(twenty_test['target'], predict))
print(classification_report(twenty_test['target'], predict))